In [ ]:
!pip install geopy hvplot optuna plotly pytz joblib tqdm bokeh cartopy geoviews pyproj bokeh_sampledata geopandas

In [1]:
import copy
import os
import sys
from scipy.spatial import ConvexHull

import geopandas as gpd
from shapely.geometry import MultiPoint, Polygon, Point
import geopy.distance
import hvplot.pandas
import numpy as np
import optuna
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import pytz
from bokeh.sampledata.penguins import data as df
import joblib
from sklearn.ensemble import RandomForestRegressor
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from sklearn.neural_network import MLPRegressor
from tqdm import tqdm
import pickle


In [2]:
input_path = r'../../data/NREL/california_2006/united_processed_data'
united_data_df = pd.read_csv(os.path.join(input_path, "united_data_2006.csv"))
sensor_location = pd.read_csv(os.path.join(input_path, "sensors_location_2006.csv"))
sensor_location
### There are few sensors at same location

ID  Latitude  Longitude
0     32.55_-117.05_DPV_13MW     32.55    -117.05
1     32.65_-115.15_UPV_75MW     32.65    -115.15
2     32.65_-116.15_UPV_50MW     32.65    -116.15
3     32.65_-116.85_UPV_38MW     32.65    -116.85
4     32.65_-116.95_DPV_12MW     32.65    -116.95
..                       ...       ...        ...
400   39.75_-121.85_DPV_11MW     39.75    -121.85
401  39.95_-122.95_UPV_100MW     39.95    -122.95
402    40.55_-122.35_DPV_6MW     40.55    -122.35
403    40.55_-122.45_DPV_6MW     40.55    -122.45
404   41.95_-122.95_UPV_11MW     41.95    -122.95

[405 rows x 3 columns]

In [3]:
def calc_convex_hull(longitudes, latitudes):
    points = list(zip(longitudes, latitudes))
    gdf = gpd.GeoDataFrame(geometry=[MultiPoint(points)])
    
    # Compute the convex hull
    convex_hull = gdf.union_all().convex_hull
    # Extract the convex hull coordinates
    if convex_hull.geom_type == 'Polygon':
        hull_coords = np.array(convex_hull.exterior.coords)
    else:
        hull_coords = np.array(convex_hull.coords)
    return hull_coords

def calc_bounding_box(longitudes, latitudes, tol):

    points = list(zip(longitudes, latitudes))
    gdf = gpd.GeoDataFrame(geometry=[MultiPoint(points)])
    
    # Compute the bounding box
    bounding_box = gdf.union_all().envelope.buffer(tol).envelope
    
    # Extract the bounding box coordinates
    if bounding_box.geom_type == 'Polygon':
        bbox_coords = np.array(bounding_box.exterior.coords)
    else:
        # For multi-polygon cases, we handle them as follows
        bbox_coords = np.array(bounding_box[0].exterior.coords)
    
    return bbox_coords


def generate_grid_within_hull(coords, grid_resolution):
    """
    Generate grid points within the convex hull defined by the coordinates.

    Parameters:
    coords (np.ndarray): Array of shape (n, 2) with longitude and latitude points of the convex hull.
    grid_resolution (float): Spacing between grid points.

    Returns:
    np.ndarray: Array of grid points (longitude, latitude) inside the convex hull.
    """
    # Create a Polygon object for the convex hull
    hull_polygon = Polygon(coords)

    # Extract bounding box
    min_lon, min_lat = np.min(coords, axis=0)
    max_lon, max_lat = np.max(coords, axis=0)

    # Generate grid points
    lon_points = np.arange(min_lon, max_lon + grid_resolution, grid_resolution)
    lat_points = np.arange(min_lat, max_lat + grid_resolution, grid_resolution)
    grid_points = np.array([[lon, lat] for lon in lon_points for lat in lat_points])

    # Filter grid points inside the convex hull
    inside_points = [point for point in grid_points if hull_polygon.contains(Point(point))]

    # Convert to numpy array for further use
    return np.array(inside_points)

In [4]:
tested_sensor_location = sensor_location.copy() #Original Grid df
lon_lat_ch = calc_bounding_box(sensor_location.Longitude.to_list(), sensor_location.Latitude.to_list(), 0.3) 
lon_lat_grid = generate_grid_within_hull(lon_lat_ch, 2e-2) #Interpulated Grid df
df_hull = pd.DataFrame(lon_lat_ch, columns=['Longitude', 'Latitude'])
df_obs_grid = pd.DataFrame(lon_lat_grid, columns=['Longitude', 'Latitude'])

lon_vec = np.sort(np.unique(df_obs_grid["Longitude"]))
lat_vec = np.sort(np.unique(df_obs_grid["Latitude"]))

coords_1 = (lat_vec[1], lon_vec[1])
coords_2 = (lat_vec[0], lon_vec[1])
coords_3 = (lat_vec[0], lon_vec[0])

lat_dist = geopy.distance.geodesic(coords_1, coords_2).km
lon_dist = geopy.distance.geodesic(coords_2, coords_3).km

print("num of sensors: " + str(len(lat_vec)) + "x" + str(len(lon_vec)))
print("X distance = " + str(lon_dist))
print("Y distance = " + str(lat_dist))
print("total X distance = " + str((len(lon_vec) - 1) * lon_dist))
print("total Y distance = " + str((len(lat_vec) - 1) * lat_dist))
print("Max Longitude = " + str(max(lon_vec)))
print("Min Longitude = " + str(min(lon_vec)))
print("Max Latitude = " + str(max(lat_vec)))
print("Min Latitude = " + str(min(lat_vec)))


# Plot new points
hull_plot = df_hull.hvplot.polygons(
    x="Longitude",
    y="Latitude",
    cmap="bwr",
    alpha = 0.2,
    geo=True,
    tiles="CartoLight"
)

obs_grid_plot = df_obs_grid.hvplot.points(
    x="Longitude",
    y="Latitude",
    alpha = 0.2,
    geo=True,
    tiles="CartoLight"
)

tested_sensor_location_plot = tested_sensor_location.hvplot.points(
    x="Longitude",
    y="Latitude",
    geo=True,
    tiles="CartoLight",
)

obs_grid_plot * tested_sensor_location_plot * hull_plot

num of sensors: 499x450
X distance = 1.8843037539374814
Y distance = 2.2178344236397143
total X distance = 846.0523855179291
total Y distance = 1104.4815429725777
Max Longitude = -114.25000000000179
Min Longitude = -123.23
Max Latitude = 42.23000000000156
Min Latitude = 32.27


:Overlay
   .WMTS.I     :WMTS   [Longitude,Latitude]
   .Points.I   :Points   [Longitude,Latitude]
   .WMTS.II    :WMTS   [Longitude,Latitude]
   .Points.II  :Points   [Longitude,Latitude]
   .WMTS.III   :WMTS   [Longitude,Latitude]
   .Polygons.I :Polygons   [Longitude,Latitude]

In [5]:
def get_meas_df(united_data_df):
    meas_df = united_data_df.copy()
    new_col_names = []
    for col in united_data_df.columns:
        if col.startswith("power_mw_") and not col.startswith("power_mw_norm_"):
            col_split = col.split("_")
            new_col = (float(col_split[2]),float(col_split[3]))
            new_col_names.append(new_col)
        else:
            new_col_names.append(col)
    new_col_names   
    meas_df.columns = new_col_names    
    return meas_df


def get_norm_meas_df(united_data_df):
    meas_df = united_data_df.copy()
    new_col_names = []
    for col in united_data_df.columns:
        if col.startswith("power_mw_norm_"):
            col_split = col.split("_")
            new_col = (float(col_split[3]),float(col_split[4]))
            new_col_names.append(new_col)
        else:
            new_col_names.append(col)
    new_col_names   
    meas_df.columns = new_col_names    
    return meas_df

In [6]:
# meas_df = united_data_df.copy()
# new_col_names = []
# kk = 0
# for col in united_data_df.columns:
#     if col.startswith("power_mw_") and not col.startswith("power_mw_norm_"):
#         col_split = col.split("_")
#         new_col = (float(col_split[2]),float(col_split[3]))
#         new_col_names.append(new_col)
#         kk+=1
#     else:
#         new_col_names.append(col)
# new_col_names   
# meas_df.columns = new_col_names
meas_df = get_meas_df(united_data_df)
norm_meas_df = get_norm_meas_df(united_data_df)

In [7]:
norm_meas_df

Time  (32.55, -117.05)   altitude     azimuth  \
0      2006-01-01 05:00:00-08:00              -0.0 -22.578007  103.672639   
1      2006-01-01 05:05:00-08:00              -0.0 -21.555681  104.241716   
2      2006-01-01 05:10:00-08:00              -0.0 -20.535930  104.812124   
3      2006-01-01 05:15:00-08:00              -0.0 -19.518861  105.384189   
4      2006-01-01 05:20:00-08:00              -0.0 -18.504585  105.958232   
...                          ...               ...        ...         ...   
61315  2006-12-31 18:35:00-08:00              -0.0 -20.924838  255.339322   
61316  2006-12-31 18:40:00-08:00              -0.0 -21.945022  255.909258   
61317  2006-12-31 18:45:00-08:00              -0.0 -22.967754  256.477972   
61318  2006-12-31 18:50:00-08:00              -0.0 -23.992928  257.045802   
61319  2006-12-31 18:55:00-08:00              -0.0 -25.020442  257.613092   

       power_mw_32.55_-117.05_DPV_13MW  csi_haurwitz  \
0                                  0.0   -489.037598   
1                                  0.0   -471.112939   
2                                  0.0   -453.130285   
3                                  0.0   -435.102165   
4                                  0.0   -417.042018   
...                                ...           ...   
61315                              0.0   -459.999974   
61316                              0.0   -477.952049   
61317                              0.0   -495.841914   
61318                              0.0   -513.657997   
61319                              0.0   -531.389251   

       power_mw_32.65_-115.15_UPV_75MW  (32.65, -115.15)  \
0                                  0.0              -0.0   
1                                  0.0              -0.0   
2                                  0.0              -0.0   
3                                  0.0              -0.0   
4                                  0.0              -0.0   
...                                ...               ...   
61315                              0.0              -0.0   
61316                              0.0              -0.0   
61317                              0.0              -0.0   
61318                              0.0              -0.0   
61319                              0.0              -0.0   

       power_mw_32.65_-116.15_UPV_50MW  (32.65, -116.15)  ...  \
0                                  0.0              -0.0  ...   
1                                  0.0              -0.0  ...   
2                                  0.0              -0.0  ...   
3                                  0.0              -0.0  ...   
4                                  0.0              -0.0  ...   
...                                ...               ...  ...   
61315                              0.0              -0.0  ...   
61316                              0.0              -0.0  ...   
61317                              0.0              -0.0  ...   
61318                              0.0              -0.0  ...   
61319                              0.0              -0.0  ...   

       power_mw_39.75_-121.85_DPV_11MW  (39.75, -121.85)  \
0                                  0.0              -0.0   
1                                  0.0              -0.0   
2                                  0.0              -0.0   
3                                  0.0              -0.0   
4                                  0.0              -0.0   
...                                ...               ...   
61315                              0.0              -0.0   
61316                              0.0              -0.0   
61317                              0.0              -0.0   
61318                              0.0              -0.0   
61319                              0.0              -0.0   

       power_mw_39.95_-122.95_UPV_100MW  (39.95, -122.95)  \
0                                   0.0              -0.0   
1                                   0.0              -0.0   
2                       

In [8]:
# import holoviews as hv


# data_vec = meas_df[(32.55, -117.05)]
# data_vec = data_vec[data_vec< 1000]

# hv.Scatter(data_vec.to_list())


In [9]:
def geodesic_distance_matrix(points):
    num_points = len(points)
    distances = np.zeros((num_points, num_points))
    for i in range(num_points):
        for j in range(num_points):
            if i != j:
                distances[i, j] = geopy.distance.geodesic(points[i], points[j]).km
            else:
                distances[i, j] = 0  # Distance to itself is 0
    return distances

def calc_distances(lon_grid, lat_grid, lon_data, lat_data):
    num_lat = lat_grid.nunique()
    num_lon = lon_grid.nunique()
    dist_matrix_path = f"distance_matrix_{num_lon}_{num_lat}.pkl"
    if os.path.exists(dist_matrix_path):
        print(f"Loading distance matrix from {dist_matrix_path}...")
        with open(dist_matrix_path, 'rb') as f:
            distances = pickle.load(f)
    else:
        print(f"Calculating distances and saving to {dist_matrix_path}...")
        grid_points = np.vstack([lat_grid, lon_grid]).T
        data_points = np.vstack([lat_data, lon_data]).T
        distances = np.array([
            [geopy.distance.geodesic(p1, p2).km for p1 in grid_points] for p2 in tqdm(data_points, desc="Calculating distances", unit="point")
        ])
        with open(dist_matrix_path, 'wb') as f:
            pickle.dump(distances, f)
    return distances


def general_idw_interpolation(distances_matrix, values, max_dist, power=2):
    values_exp = np.expand_dims(values, axis = 1)
    distances = distances_matrix.copy()
    distances[distances > max_dist] = np.inf
    distances_exp = np.expand_dims(distances, axis = 2)
    weights = 1 / ((distances_exp)**power+1)
    weighted_values = np.sum(weights * values_exp, axis=0)
    sum_weights = np.sum(weights, axis=0)
    is_close_enough = (np.min(distances_exp, axis=0) <= max_dist).astype(int)
    idw_interp =  (weighted_values / (sum_weights+1e-6))*is_close_enough
    return idw_interp


def idw_interpolation(distances_matrix, values, max_dist, power=2):
    distances = distances_matrix.copy()
    distances[distances > max_dist] = np.inf
    weights = 1 / ((distances)**power+1)
    weighted_values = np.sum(weights * values, axis=0)
    sum_weights = np.sum(weights, axis=0)
    is_close_enough = (np.min(distances_matrix, axis=0) <= max_dist).astype(int)
    idw_interp =  (weighted_values / (sum_weights+1e-6))*is_close_enough
    return idw_interp
    

In [10]:
example_idx = 31910
tested_meas_df = meas_df.drop(columns=[col for col in meas_df.columns if not isinstance(col, tuple)]).iloc[example_idx]
val_list = np.array(tested_meas_df.to_list())
values = val_list[:, np.newaxis]


lat_list = np.array([col[0] for col in tested_meas_df.index])
lon_list = np.array([col[1] for col in tested_meas_df.index])

lon_grid = df_obs_grid.Longitude
lat_grid = df_obs_grid.Latitude
lon_data = lon_list
lat_data = lat_list

tested_norm_meas_df = norm_meas_df.drop(columns=[col for col in norm_meas_df.columns if not isinstance(col, tuple)]).iloc[example_idx]
norm_val_list = np.array(tested_norm_meas_df.to_list())
norm_values = norm_val_list[:, np.newaxis]

In [11]:
distances_matrix = calc_distances(lon_grid, lat_grid, lon_data, lat_data)

Loading distance matrix from distance_matrix_450_499.pkl...


In [ ]:
idx = 31910
step = 100
value_mat = meas_df.drop(columns=[col for col in meas_df.columns if not isinstance(col, tuple)]).to_numpy()
grid_interp_full = general_idw_interpolation(distances_matrix, value_mat.T[:,idx:idx+step], 30, power=2)


In [ ]:
tested_sensor_location['vals'] = values
df_obs_grid['vals'] = idw_interpolation(distances_matrix, values, 30, power=2)


obs_grid_plot = df_obs_grid.hvplot.points(
    x="Longitude",
    y="Latitude",
    color="vals",  # Use the 'vals' column for coloring
    cmap="viridis",  # Specify a colormap (you can choose your preferred one)
    alpha=0.8,  # Adjust transparency for better visibility
    geo=True,
    tiles="CartoLight"
)

tested_sensor_location_plot = tested_sensor_location.hvplot.points(
    x="Longitude",
    y="Latitude",
    color="vals",  # Use the 'vals' column for coloring
    cmap="viridis",  # Specify a colormap
    geo=True,
    tiles="CartoLight"
)

obs_grid_plot + tested_sensor_location_plot

In [ ]:
tested_sensor_location['vals'] = norm_values
df_obs_grid['vals'] = idw_interpolation(distances_matrix, norm_values, 30, power=2)


obs_grid_plot = df_obs_grid.hvplot.points(
    x="Longitude",
    y="Latitude",
    color="vals",  # Use the 'vals' column for coloring
    cmap="viridis",  # Specify a colormap (you can choose your preferred one)
    alpha=0.8,  # Adjust transparency for better visibility
    geo=True,
    tiles="CartoLight"
)

tested_sensor_location_plot = tested_sensor_location.hvplot.points(
    x="Longitude",
    y="Latitude",
    color="vals",  # Use the 'vals' column for coloring
    cmap="viridis",  # Specify a colormap
    geo=True,
    tiles="CartoLight"
)

obs_grid_plot + tested_sensor_location_plot

In [ ]:

# aaa = idw_interpolation(distances_matrix, value_mat[31910, :][:, np.newaxis], 30, power=2)
# bbb = general_idw_interpolation(distances_matrix, value_mat.T[:,31910:31912], 30, power=2)

In [ ]:
import os
import pandas as pd
import plotly.express as px
import geopy
coords_1 = sensor_location.iloc[0][['Latitude', 'Longitude']].tolist()
coords_2 = sensor_location.iloc[1][['Latitude', 'Longitude']].tolist()
geopy.distance.geodesic(coords_1, coords_2).km

In [ ]:
i = 300
example_file_name = all_files_list[i]
example_df = pd.read_csv(os.path.join(input_path, example_file_name))
example_df['LocalTime'] = pd.to_datetime(example_df['LocalTime'])
example_df.rename(columns={"Power(MW)": "power_mw", "LocalTime": "local_time"}, inplace=True)
example_df

In [ ]:
px.line(x=example_df.local_time, y=example_df.power_mw).show()